<a href="https://colab.research.google.com/github/kimo722504/practice_ML/blob/master/practice_object_detection_api.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Object detection api
[영상](https://www.youtube.com/watch?v=Rgpfk6eYxJA&t=803s)을 그대로 따라 했고, *버전*으로 인한 에러를 *Notebook*에 맞게 수정하였습니다.
colab에서 ipynb 파일을 키고 그대로 따라 하시면 됩니다. 


영상의 virtualenv, conda 설정 부분은 대부분 하지 않고 진행하였습니다. 
**colab**을 사용하기 때문에 대부분 편하게 사용할 수 있습니다. Good~!

1. colab 들어감.
1. File > Open notebook > object_detection_training_kimo.ipynb
1. Runtime > Change Runtime Type > Hardware Accelerator > GPU 클릭
1. 다른 거 할 필요 없이 **셀**만 실행하면 됨.

>  참고 : [영상](https://www.youtube.com/watch?v=Rgpfk6eYxJA&t=803s)을 먼저 한번 보고오시면 따라할때 더욱더 이해가 잘됩니다.

## tensorflow 버젼 맞춰주기
colab에는 기본적으로 텐서플로우가 설치되어있지만 영상과 버젼을 맞춰줍니다.

> **중요** : Runtime 을 GPU로 변경하셨나요?? 안하셨다면 변경먼저하세요~!

In [0]:
!pip3 install tensorflow-gpu==1.12.0

     |████████████████████████████████| 281.7MB 101kB/s 
     |████████████████████████████████| 3.1MB 43.3MB/s 
ERROR: tensorflow 1.14.0 has requirement tensorboard<1.15.0,>=1.14.0, but you'll have tensorboard 1.12.2 which is incompatible.
  Found existing installation: tensorboard 1.14.0
    Uninstalling tensorboard-1.14.0:
      Successfully uninstalled tensorboard-1.14.0


In [0]:
!wget https://developer.nvidia.com/compute/cuda/9.0/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
!dpkg -i cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
!apt-key add /var/cuda-repo-9-0-local/7fa2af80.pub
!apt-get update
!apt-get install cuda=9.0.176-1

--2019-07-15 06:00:41--  https://developer.nvidia.com/compute/cuda/9.0/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
Resolving developer.nvidia.com (developer.nvidia.com)... 192.229.189.146
Connecting to developer.nvidia.com (developer.nvidia.com)|192.229.189.146|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://developer.download.nvidia.com/compute/cuda/9.0/secure/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64.deb?7a-0yqMJG9Vk0uJOjbYRNbrswDrzhMNGgtZCzVxydnJmzofF1E-FmW380F1cEe7ElGU1H5dNLdpNVBxgQpElqYYmYBwxy4qErl-Tz5qLmFLQ2JhZ2iBL63zGERvzaFnpfNpxpmAYIhb-9jXx0ezUQ25dAKe7FxuQjOimtHwOixIN7emOBDovuyXKSDXdOQpfYXbH9bdcM-ys7F3WsOEA [following]
--2019-07-15 06:00:41--  https://developer.download.nvidia.com/compute/cuda/9.0/secure/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64.deb?7a-0yqMJG9Vk0uJOjbYRNbrswDrzhMNGgtZCzVxydnJmzofF1E-FmW380F1cEe7ElGU1H5dNLdpNVBxgQpElqYYmYBwxy4qErl-Tz5qLmFLQ2J

In [0]:
import tensorflow as tf
print(tf.__version__)

1.12.0


In [0]:
!git clone https://github.com/tensorflow/models

Cloning into 'models'...
remote: Enumerating objects: 5, done.
remote: Counting objects: 100% (5/5), done.
remote: Compressing objects: 100% (5/5), done.
remote: Total 28282 (delta 0), reused 1 (delta 0), pack-reused 28277
Receiving objects: 100% (28282/28282), 509.37 MiB | 9.51 MiB/s, done.
Resolving deltas: 100% (17432/17432), done.
Checking out files: 100% (3005/3005), done.


## coco trained-models 중 하나인 faster_rcnn_inception_v2_coco 파일을 다운로드
영상에서는 클릭해서 다운받지만 우리는 코드로 받아봅시다.

In [0]:
import requests
filename = "faster_rcnn_inception_v2_coco_2018_01_28.tar.gz"
URL = "http://download.tensorflow.org/models/object_detection/"+filename
response = requests.get(URL,stream=True)
if response.status_code == 200:
    with open("/content/models/research/object_detection/"+filename, 'wb') as f:
        f.write(response.content) # 파일저장하기

## 다운 받은파일 압축해제

In [0]:
%cd /content/models/research/object_detection/
!tar -xvzf faster_rcnn_inception_v2_coco_2018_01_28.tar.gz

/content/models/research/object_detection
faster_rcnn_inception_v2_coco_2018_01_28/
faster_rcnn_inception_v2_coco_2018_01_28/model.ckpt.index
faster_rcnn_inception_v2_coco_2018_01_28/checkpoint
faster_rcnn_inception_v2_coco_2018_01_28/pipeline.config
faster_rcnn_inception_v2_coco_2018_01_28/model.ckpt.data-00000-of-00001
faster_rcnn_inception_v2_coco_2018_01_28/model.ckpt.meta
faster_rcnn_inception_v2_coco_2018_01_28/saved_model/
faster_rcnn_inception_v2_coco_2018_01_28/saved_model/saved_model.pb
faster_rcnn_inception_v2_coco_2018_01_28/saved_model/variables/
faster_rcnn_inception_v2_coco_2018_01_28/frozen_inference_graph.pb


In [0]:
!pwd
!ls -al

/content/models/research/object_detection
total 146112
drwxr-xr-x 26 root   root      4096 Jul 15 06:07 .
drwxr-xr-x 70 root   root      4096 Jul 15 06:05 ..
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 anchor_generators
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 box_coders
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 builders
-rw-r--r--  1 root   root       765 Jul 15 06:04 CONTRIBUTING.md
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 core
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 data
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 data_decoders
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 dataset_tools
drwxr-xr-x  3 root   root      4096 Jul 15 06:04 dockerfiles
-rw-r--r--  1 root   root     42651 Jul 15 06:04 eval_util.py
-rw-r--r--  1 root   root     11726 Jul 15 06:04 eval_util_test.py
-rw-r--r--  1 root   root     20987 Jul 15 06:04 exporter.py
-rw-r--r--  1 root   root     50337 Jul 15 06:04 exporter_test.py
-rw-r--r--  1 root   root      6852 Jul 1

In [0]:
!git clone https://github.com/EdjeElectronics/TensorFlow-Object-Detection-API-Tutorial-Train-Multiple-Objects-Windows-10

Cloning into 'TensorFlow-Object-Detection-API-Tutorial-Train-Multiple-Objects-Windows-10'...
remote: Enumerating objects: 47, done.
remote: Counting objects: 100% (47/47), done.
remote: Compressing objects: 100% (47/47), done.
remote: Total 1092 (delta 29), reused 1 (delta 0), pack-reused 1045
Receiving objects: 100% (1092/1092), 57.61 MiB | 903.00 KiB/s, done.
Resolving deltas: 100% (544/544), done.


## cp f 옵션은 덮어쓰기
아래 셀까지 실행하면 유튜브 영상의 6:35까지 한거임

In [0]:
!cp -rf TensorFlow-Object-Detection-API-Tutorial-Train-Multiple-Objects-Windows-10/* ./

In [0]:
!pwd
!ls -al

/content/models/research/object_detection
total 166412
drwxr-xr-x 31 root   root      4096 Jul 15 06:08 .
drwxr-xr-x 70 root   root      4096 Jul 15 06:05 ..
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 anchor_generators
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 box_coders
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 builders
-rw-r--r--  1 root   root       765 Jul 15 06:04 CONTRIBUTING.md
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 core
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 data
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 data_decoders
drwxr-xr-x  2 root   root      4096 Jul 15 06:04 dataset_tools
drwxr-xr-x  2 root   root      4096 Jul 15 06:08 doc
drwxr-xr-x  3 root   root      4096 Jul 15 06:04 dockerfiles
-rw-r--r--  1 root   root     42651 Jul 15 06:04 eval_util.py
-rw-r--r--  1 root   root     11726 Jul 15 06:04 eval_util_test.py
-rw-r--r--  1 root   root     20987 Jul 15 06:04 exporter.py
-rw-r--r--  1 root   root     50337 Jul 15 06:04 expor

## 가상환경 pythonpath를 설정하는 부분 (영상 12:40)
pythonpath를 설정하지 않으면 경로를 찾지못해서 *import* 에러가 납니다.   
우리는 가상화를 하지 않았기때문에 아래와 같은 방법으로 pythonpath를 설정해줍시다.


In [0]:
import sys
sys.path.append('/content/models/')
sys.path.append('/content/models/research/')
sys.path.append('/content/models/research/slim')


In [0]:
cd /content/models/research/object_detection

/content/models/research/object_detection


## protoc 컴파일 하는법 (영상 13:22)
이부분이 좀 귀찮은데 우리는 .proto 파일을 .py파일로 변환해야합니다.  
protoc 명령을 사용해야하는데 영상에서는 conda install 로 간단히 설치했습니다. (영상 10:04)  

In [0]:
import requests
filename = "protobuf-python-3.8.0.tar.gz"
URL = "https://github.com/protocolbuffers/protobuf/releases/download/v3.8.0/"+filename
response = requests.get(URL,stream=True)
if response.status_code == 200:
    with open("/content/models/research/object_detection/"+filename, 'wb') as f:
        f.write(response.content)

In [0]:
!tar -xvzf protobuf-python-3.8.0.tar.gz

protobuf-3.8.0/
protobuf-3.8.0/config.sub
protobuf-3.8.0/editors/
protobuf-3.8.0/editors/proto.vim
protobuf-3.8.0/editors/protobuf-mode.el
protobuf-3.8.0/editors/README.txt
protobuf-3.8.0/CHANGES.txt
protobuf-3.8.0/README.md
protobuf-3.8.0/generate_descriptor_proto.sh
protobuf-3.8.0/missing
protobuf-3.8.0/depcomp
protobuf-3.8.0/ltmain.sh
protobuf-3.8.0/autogen.sh
protobuf-3.8.0/compile
protobuf-3.8.0/conformance/
protobuf-3.8.0/conformance/conformance_cpp.cc
protobuf-3.8.0/conformance/failure_list_js.txt
protobuf-3.8.0/conformance/README.md
protobuf-3.8.0/conformance/text_format_conformance_suite.h
protobuf-3.8.0/conformance/failure_list_php.txt
protobuf-3.8.0/conformance/failure_list_ruby.txt
protobuf-3.8.0/conformance/failure_list_cpp.txt
protobuf-3.8.0/conformance/failure_list_php_c.txt
protobuf-3.8.0/conformance/ConformanceJava.java
protobuf-3.8.0/conformance/Makefile.am
protobuf-3.8.0/conformance/conformance.proto
protobuf-3.8.0/conformance/third_party/
protobuf-3.8.0/conformance/

In [0]:
%cd /content/models/research/object_detection/protobuf-3.8.0/

/content/models/research/object_detection/protobuf-3.8.0


## protobuf install
protoc 명령어를 사용하기 위해 install 해줘야합니다.  
시간이 오래걸리므로 돌려놓고 동영상을 보던지 청소기를 돌리고 오면 됩니다.!!  
30분~1시간소요

```
!./configure
!make
!make check
!make install
%cd /content/models/research/
!ls -al ./object_detection/protos/
!ldconfig
!protoc --python_out=. ./object_detection/protos/anchor_generator.proto ./object_detection/protos/argmax_matcher.proto ./object_detection/protos/bipartite_matcher.proto ./object_detection/protos/box_coder.proto ./object_detection/protos/box_predictor.proto ./object_detection/protos/eval.proto ./object_detection/protos/faster_rcnn.proto ./object_detection/protos/faster_rcnn_box_coder.proto ./object_detection/protos/grid_anchor_generator.proto ./object_detection/protos/hyperparams.proto ./object_detection/protos/image_resizer.proto ./object_detection/protos/input_reader.proto ./object_detection/protos/losses.proto ./object_detection/protos/matcher.proto ./object_detection/protos/mean_stddev_box_coder.proto ./object_detection/protos/model.proto ./object_detection/protos/optimizer.proto ./object_detection/protos/pipeline.proto ./object_detection/protos/post_processing.proto ./object_detection/protos/preprocessor.proto ./object_detection/protos/region_similarity_calculator.proto ./object_detection/protos/square_box_coder.proto ./object_detection/protos/ssd.proto ./object_detection/protos/ssd_anchor_generator.proto ./object_detection/protos/string_int_label_map.proto ./object_detection/protos/train.proto ./object_detection/protos/keypoint_box_coder.proto ./object_detection/protos/multiscale_anchor_generator.proto ./object_detection/protos/graph_rewriter.proto ./object_detection/protos/calibration.proto ./object_detection/protos/flexible_grid_anchor_generator.proto


```
출처: https://notetoday.tistory.com/entry/Ubuntu-Protocol-Buffer-설치-protoc [하루노트]

# 하지만 !!!!!!!!!!!!!!
우리는 **30분**이라는 시간을 기다릴순없습니다..  
제가 미리 변환해놓은 파일을 클론해서 그대로 사용합시다.  
~정석대로하고싶다면 위에있는대로 하면됨~

In [0]:
%cd /content/models/research/object_detection/protos/
!rm -rf /content/models/research/object_detection/protos/*
!git clone https://github.com/kimo722504/pb2 .

/content/models/research/object_detection/protos
Cloning into '.'...
remote: Enumerating objects: 65, done.
remote: Counting objects: 100% (65/65), done.
remote: Compressing objects: 100% (32/32), done.
remote: Total 65 (delta 32), reused 65 (delta 32), pack-reused 0
Unpacking objects: 100% (65/65), done.


In [0]:
!pwd
!ls -al 

/content/models/research/object_detection/protos
total 708
drwxr-xr-x  3 root root   4096 Jul 15 06:09 .
drwxr-xr-x 32 root root   4096 Jul 15 06:09 ..
-rw-r--r--  1 root root   6979 Jul 15 06:09 anchor_generator_pb2.py
-rw-r--r--  1 root root    747 Jul 15 06:09 anchor_generator.proto
-rw-r--r--  1 root root   4546 Jul 15 06:09 argmax_matcher_pb2.py
-rw-r--r--  1 root root   1151 Jul 15 06:09 argmax_matcher.proto
-rw-r--r--  1 root root   2222 Jul 15 06:09 bipartite_matcher_pb2.py
-rw-r--r--  1 root root    350 Jul 15 06:09 bipartite_matcher.proto
-rw-r--r--  1 root root   6339 Jul 15 06:09 box_coder_pb2.py
-rw-r--r--  1 root root    656 Jul 15 06:09 box_coder.proto
-rw-r--r--  1 root root  37394 Jul 15 06:09 box_predictor_pb2.py
-rw-r--r--  1 root root   7365 Jul 15 06:09 box_predictor.proto
-rw-r--r--  1 root root  21873 Jul 15 06:09 calibration_pb2.py
-rw-r--r--  1 root root   2057 Jul 15 06:09 calibration.proto
-rw-r--r--  1 root root  12935 Jul 15 06:09 eval_pb2.py
-rw-r--r--  1 

In [0]:
%cd /content/models/research/
!python setup.py build
!python setup.py install


/content/models/research
running build
running build_py
creating build
creating build/lib
creating build/lib/object_detection
copying object_detection/Object_detection_webcam.py -> build/lib/object_detection
copying object_detection/model_tpu_main.py -> build/lib/object_detection
copying object_detection/eval_util.py -> build/lib/object_detection
copying object_detection/generate_tfrecord.py -> build/lib/object_detection
copying object_detection/export_tflite_ssd_graph.py -> build/lib/object_detection
copying object_detection/exporter.py -> build/lib/object_detection
copying object_detection/model_lib_test.py -> build/lib/object_detection
copying object_detection/export_inference_graph.py -> build/lib/object_detection
copying object_detection/model_lib.py -> build/lib/object_detection
copying object_detection/model_main.py -> build/lib/object_detection
copying object_detection/eval_util_test.py -> build/lib/object_detection
copying object_detection/inputs.py -> build/lib/object_detecti

In [0]:
%cd /content/models/research/object_detection

/content/models/research/object_detection


## 코드실행
여기까지 하면 셋업이 완료되었습니다. 축하합니다~~~  
object_detection_tutorial.ipynb 파일을 켜서 그대로 파이썬 코드를 실행시키면됩니다.  
아래의 내용은 [https://github.com/tensorflow/.../object_detection_tutorial.ipynb](https://github.com/tensorflow/models/blob/master/research/object_detection/object_detection_tutorial.ipynb) 파일 내용을 그대로 옮긴 것입니다

# Object Detection Demo
Welcome to the object detection inference walkthrough!  This notebook will walk you step by step through the process of using a pre-trained model to detect objects in an image. Make sure to follow the [installation instructions](https://github.com/tensorflow/models/blob/master/research/object_detection/g3doc/installation.md) before you start.

# Imports

In [0]:
import numpy as np
import os
import six.moves.urllib as urllib
import sys
import tarfile
import tensorflow as tf
import zipfile

from distutils.version import StrictVersion
from collections import defaultdict
from io import StringIO
from matplotlib import pyplot as plt
from PIL import Image

# This is needed since the notebook is stored in the object_detection folder.
sys.path.append("..")
from object_detection.utils import ops as utils_ops

if StrictVersion(tf.__version__) < StrictVersion('1.12.0'):
  raise ImportError('Please upgrade your TensorFlow installation to v1.12.*.')


## Env setup

In [0]:
# This is needed to display the images.
%matplotlib inline

## Object detection imports
Here are the imports from the object detection module.

In [0]:
from utils import label_map_util

from utils import visualization_utils as vis_util

# Model preparation 

## Variables

Any model exported using the `export_inference_graph.py` tool can be loaded here simply by changing `PATH_TO_FROZEN_GRAPH` to point to a new .pb file.  

By default we use an "SSD with Mobilenet" model here. See the [detection model zoo](https://github.com/tensorflow/models/blob/master/research/object_detection/g3doc/detection_model_zoo.md) for a list of other models that can be run out-of-the-box with varying speeds and accuracies.

In [0]:
# What model to download.
MODEL_NAME = 'ssd_mobilenet_v1_coco_2017_11_17'
MODEL_FILE = MODEL_NAME + '.tar.gz'
DOWNLOAD_BASE = 'http://download.tensorflow.org/models/object_detection/'

# Path to frozen detection graph. This is the actual model that is used for the object detection.
PATH_TO_FROZEN_GRAPH = MODEL_NAME + '/frozen_inference_graph.pb'

# List of the strings that is used to add correct label for each box.
PATH_TO_LABELS = os.path.join('data', 'mscoco_label_map.pbtxt')

## Download Model

In [0]:
opener = urllib.request.URLopener()
opener.retrieve(DOWNLOAD_BASE + MODEL_FILE, MODEL_FILE)
tar_file = tarfile.open(MODEL_FILE)
for file in tar_file.getmembers():
  file_name = os.path.basename(file.name)
  if 'frozen_inference_graph.pb' in file_name:
    tar_file.extract(file, os.getcwd())

## Load a (frozen) Tensorflow model into memory.

In [0]:
detection_graph = tf.Graph()
with detection_graph.as_default():
  od_graph_def = tf.GraphDef()
  with tf.gfile.GFile(PATH_TO_FROZEN_GRAPH, 'rb') as fid:
    serialized_graph = fid.read()
    od_graph_def.ParseFromString(serialized_graph)
    tf.import_graph_def(od_graph_def, name='')

## Loading label map
Label maps map indices to category names, so that when our convolution network predicts `5`, we know that this corresponds to `airplane`.  Here we use internal utility functions, but anything that returns a dictionary mapping integers to appropriate string labels would be fine

In [0]:
category_index = label_map_util.create_category_index_from_labelmap(PATH_TO_LABELS, use_display_name=True)

## Helper code

In [0]:
def load_image_into_numpy_array(image):
  (im_width, im_height) = image.size
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)

# Detection

In [0]:
# For the sake of simplicity we will use only 2 images:
# image1.jpg
# image2.jpg
# If you want to test the code with your images, just add path to the images to the TEST_IMAGE_PATHS.
PATH_TO_TEST_IMAGES_DIR = 'test_images'
TEST_IMAGE_PATHS = [ os.path.join(PATH_TO_TEST_IMAGES_DIR, 'image{}.jpg'.format(i)) for i in range(1, 3) ]

# Size, in inches, of the output images.
IMAGE_SIZE = (12, 8)

In [0]:
def run_inference_for_single_image(image, graph):
  with graph.as_default():
    with tf.Session() as sess:
      # Get handles to input and output tensors
      ops = tf.get_default_graph().get_operations()
      all_tensor_names = {output.name for op in ops for output in op.outputs}
      tensor_dict = {}
      for key in [
          'num_detections', 'detection_boxes', 'detection_scores',
          'detection_classes', 'detection_masks'
      ]:
        tensor_name = key + ':0'
        if tensor_name in all_tensor_names:
          tensor_dict[key] = tf.get_default_graph().get_tensor_by_name(
              tensor_name)
      if 'detection_masks' in tensor_dict:
        # The following processing is only for single image
        detection_boxes = tf.squeeze(tensor_dict['detection_boxes'], [0])
        detection_masks = tf.squeeze(tensor_dict['detection_masks'], [0])
        # Reframe is required to translate mask from box coordinates to image coordinates and fit the image size.
        real_num_detection = tf.cast(tensor_dict['num_detections'][0], tf.int32)
        detection_boxes = tf.slice(detection_boxes, [0, 0], [real_num_detection, -1])
        detection_masks = tf.slice(detection_masks, [0, 0, 0], [real_num_detection, -1, -1])
        detection_masks_reframed = utils_ops.reframe_box_masks_to_image_masks(
            detection_masks, detection_boxes, image.shape[1], image.shape[2])
        detection_masks_reframed = tf.cast(
            tf.greater(detection_masks_reframed, 0.5), tf.uint8)
        # Follow the convention by adding back the batch dimension
        tensor_dict['detection_masks'] = tf.expand_dims(
            detection_masks_reframed, 0)
      image_tensor = tf.get_default_graph().get_tensor_by_name('image_tensor:0')

      # Run inference
      output_dict = sess.run(tensor_dict,
                             feed_dict={image_tensor: image})

      # all outputs are float32 numpy arrays, so convert types as appropriate
      output_dict['num_detections'] = int(output_dict['num_detections'][0])
      output_dict['detection_classes'] = output_dict[
          'detection_classes'][0].astype(np.int64)
      output_dict['detection_boxes'] = output_dict['detection_boxes'][0]
      output_dict['detection_scores'] = output_dict['detection_scores'][0]
      if 'detection_masks' in output_dict:
        output_dict['detection_masks'] = output_dict['detection_masks'][0]
  return output_dict

In [0]:
for image_path in TEST_IMAGE_PATHS:
  image = Image.open(image_path)
  # the array based representation of the image will be used later in order to prepare the
  # result image with boxes and labels on it.
  image_np = load_image_into_numpy_array(image)
  # Expand dimensions since the model expects images to have shape: [1, None, None, 3]
  image_np_expanded = np.expand_dims(image_np, axis=0)
  # Actual detection.
  output_dict = run_inference_for_single_image(image_np_expanded, detection_graph)
  # Visualization of the results of a detection.
  vis_util.visualize_boxes_and_labels_on_image_array(
      image_np,
      output_dict['detection_boxes'],
      output_dict['detection_classes'],
      output_dict['detection_scores'],
      category_index,
      instance_masks=output_dict.get('detection_masks'),
      use_normalized_coordinates=True,
      line_thickness=8)
  plt.figure(figsize=IMAGE_SIZE)
  plt.imshow(image_np)

## images 폴더에 내용물 확인하기
카드 이미지들이 들어가있는것을 알 수 있습니다.

In [0]:
!pwd
PATH_TO_TEST_IMAGES_DIR = "images/test"
TEST_IMAGE_PATHS =  os.path.join(PATH_TO_TEST_IMAGES_DIR, "IMG_2383.JPG" )
image = Image.open(TEST_IMAGE_PATHS)
image_np = load_image_into_numpy_array(image)          
plt.imshow(image_np)                              

/content/models/research/object_detection


## xml을 csv 로 만들기

In [0]:
!python xml_to_csv.py

Successfully converted xml to csv.
Successfully converted xml to csv.


## record 파일 만들기(영상 19:35)

In [0]:
!python generate_tfrecord.py --csv_input=images/train_labels.csv --image_dir=images/train --output_path=train.record
!python generate_tfrecord.py --csv_input=images/test_labels.csv --image_dir=images/test --output_path=test.record

Successfully created the TFRecords: /content/models/research/object_detection/train.record
Successfully created the TFRecords: /content/models/research/object_detection/test.record


## 레이블 맵 만들기, config 파일 설정하기 (20:20)

In [0]:
%cd /content/models/research/object_detection/training/
!ls -al
!cat labelmap.pbtxt

/content/models/research/object_detection/training
total 16
drwxr-xr-x  2 root root 4096 Jul 15 06:08 .
drwxr-xr-x 34 root root 4096 Jul 15 06:12 ..
-rw-r--r--  1 root root 3958 Jul 15 06:08 faster_rcnn_inception_v2_pets.config
-rw-r--r--  1 root root  225 Jul 15 06:08 labelmap.pbtxt
item {
  id: 1
  name: 'nine'
}

item {
  id: 2
  name: 'ten'
}

item {
  id: 3
  name: 'jack'
}

item {
  id: 4
  name: 'queen'
}

item {
  id: 5
  name: 'king'
}

item {
  id: 6
  name: 'ace'
}


## 텍스트 치환
sed command 를 사용해 윈도우 경로인 C:/tensorflow를 적당히 치환함  
원래 영상은 **윈도우** 경로라서 그것을 colab에 맞게 수정해야함. 

> C:/tensorflow1/ 를  /content 로 변환함

In [0]:
!sed -i 's/C:\/tensorflow1/\/content/g' faster_rcnn_inception_v2_pets.config

## legacy 에서 train.py 꺼내옴
[EdjeElectronics 깃허브](https://github.com/EdjeElectronics/TensorFlow-Object-Detection-API-Tutorial-Train-Multiple-Objects-Windows-10) 설명 참고

In [0]:
%cd /content/models/research/object_detection/
!cp legacy/train.py ./

/content/models/research/object_detection


## train.py에도 path 경로 추가하기
안하면 path 설정이 안먹어서 import 에러나옴

import sys부터  
sys.path.append 까지 전부 train.py맨 윗부분에 추가

In [0]:
!echo "import sys" > for_path.py
!echo "sys.path.append('/content/models/')" >> for_path.py
!echo "sys.path.append('/content/models/research')" >> for_path.py
!echo "sys.path.append('/content/models/research/slim')" >> for_path.py

In [0]:
!cat train.py >> for_path.py
!rm train.py
!mv for_path.py train.py 

## 오류해결을 위해 config파일 수정
python train.py를 했더니  

raise ValueError('First step cannot be zero.')  
ValueError: First step cannot be zero.
라는 에러가 나온다.. 수정하기위해 91번째줄에서 94번째줄까지 지웠다.

In [0]:
!cat -n /content/models/research/object_detection/training/faster_rcnn_inception_v2_pets.config
!sed -i '91,94d' training/faster_rcnn_inception_v2_pets.config


     1	# Faster R-CNN with Inception v2, configured for Oxford-IIIT Pets Dataset.
     2	# Users should configure the fine_tune_checkpoint field in the train config as
     3	# well as the label_map_path and input_path fields in the train_input_reader and
     4	# eval_input_reader. Search for "PATH_TO_BE_CONFIGURED" to find the fields that
     5	# should be configured.
     6	
     7	model {
     8	  faster_rcnn {
     9	    num_classes: 6
    10	    image_resizer {
    11	      keep_aspect_ratio_resizer {
    12	        min_dimension: 600
    13	        max_dimension: 1024
    14	      }
    15	    }
    16	    feature_extractor {
    17	      type: 'faster_rcnn_inception_v2'
    18	      first_stage_features_stride: 16
    19	    }
    20	    first_stage_anchor_generator {
    21	      grid_anchor_generator {
    22	        scales: [0.25, 0.5, 1.0, 2.0]
    23	        aspect_ratios: [0.5, 1.0, 2.0]
    24	        height_stride: 16
    25	        width_stride: 16
    26	      }
    

In [0]:
!pip install tensorboardcolab
from tensorboardcolab import TensorBoardColab, TensorBoardColabCallback
tbc=TensorBoardColab() # 밑에 Tensorboard 를 볼 수 있는 주소가 나오니 다른창으로 들어가세요~!


Using TensorFlow backend.


Wait for 8 seconds...
TensorBoard link:
https://ce7c30e3.ngrok.io


In [0]:
!python train.py --logtostderr --train_dir=training/ --pipeline_config_path=training/faster_rcnn_inception_v2_pets.config

Instructions for updating:
Use object_detection/model_main.py.
Instructions for updating:
Please switch to tf.train.create_global_step
Instructions for updating:
Use `tf.data.experimental.parallel_interleave(...)`.
Instructions for updating:
Create a `tf.sparse.SparseTensor` and use `tf.sparse.to_dense` instead.
Instructions for updating:
Queue-based input pipelines have been replaced by `tf.data`. Use `tf.data.Dataset.batch(batch_size)` (or `padded_batch(...)` if `dynamic_pad=True`).
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
INFO:tensorflow:Scale of 0 disables regularizer.
INFO:tensorflow:Scale of 0 disables regularizer.
INFO:tensorflow:depth of additional conv before box predictor: 0
Instructions for updating:
keep_dims is deprecated, use keepdims instead
INFO:tensorflow:Scale of 0 disables regularizer.
INFO:tensorflow:Scale of 0 disables regularizer.
Instructio

# 중요 !!!
## 가장 큰 숫자 찾기

텐서플로우는 object_detection/training/ 에 5분마다 체크포인트를 기록합니다.  
ls -al 하면  
model.ckpt-XXXX 중 **가장 큰 숫자**를 찾습니다

In [0]:
ls -al training/

total 568424
drwxr-xr-x  2 root root      4096 Jul 15 07:31 ./
drwxr-xr-x 34 root root      4096 Jul 15 06:12 ../
-rw-r--r--  1 root root       277 Jul 15 07:31 checkpoint
-rw-r--r--  1 root root  28341224 Jul 15 07:33 events.out.tfevents.1563171699.0d71fa6cc3e2
-rw-r--r--  1 root root      3842 Jul 15 06:13 faster_rcnn_inception_v2_pets.config
-rw-r--r--  1 root root  10461833 Jul 15 06:21 graph.pbtxt
-rw-r--r--  1 root root       225 Jul 15 06:08 labelmap.pbtxt
-rw-r--r--  1 root root 103173376 Jul 15 06:51 model.ckpt-10126.data-00000-of-00001
-rw-r--r--  1 root root     25563 Jul 15 06:51 model.ckpt-10126.index
-rw-r--r--  1 root root   5440278 Jul 15 06:51 model.ckpt-10126.meta
-rw-r--r--  1 root root 103173376 Jul 15 07:01 model.ckpt-13552.data-00000-of-00001
-rw-r--r--  1 root root     25563 Jul 15 07:01 model.ckpt-13552.index
-rw-r--r--  1 root root   5440278 Jul 15 07:01 model.ckpt-13552.meta
-rw-r--r--  1 root root 103173376 Jul 15 07:11 model.ckpt-17000.data-00000-of-00001
-r

## XXXX를 가장 큰 숫자로 변경
밑에 커맨드 중 XXXX라고 적혀있는 부분을 **가장 큰 숫자**로 변경하고 돌리면 됩니다.(가장 최근에 생성된 파일)  
그렇게하면 inference_graph/ 밑에 pb 파일이 생성되며 그 pb파일을 로컬로 다운받아서 사용하시면 됩니다.
```
!python export_inference_graph.py --input_type image_tensor --pipeline_config_path training/faster_rcnn_inception_v2_pets.config --trained_checkpoint_prefix training/model.ckpt-XXXX --output_directory inference_graph
```

In [0]:
!echo "import sys" > for_path.py
!echo "sys.path.append('/content/models/')" >> for_path.py
!echo "sys.path.append('/content/models/research')" >> for_path.py
!echo "sys.path.append('/content/models/research/slim')" >> for_path.py

In [0]:
!cat export_inference_graph.py >> for_path.py
!rm export_inference_graph.py
!mv for_path.py export_inference_graph.py 

In [0]:
!python export_inference_graph.py --input_type image_tensor --pipeline_config_path training/faster_rcnn_inception_v2_pets.config --trained_checkpoint_prefix training/model.ckpt-23908 --output_directory inference_graph

Instructions for updating:
keep_dims is deprecated, use keepdims instead
Instructions for updating:
Please switch to tf.train.get_or_create_global_step
Instructions for updating:
Use `tf.profiler.profile(graph, run_meta, op_log, cmd, options)`. Build `options` with `tf.profiler.ProfileOptionBuilder`. See README.md for details
273 ops no flops stats due to incomplete shapes.
Parsing Inputs...
Incomplete shape.

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              0
-min_occurrence             0
-step                       -1
-order_by                   name
-account_type_regexes       _trainable_variables
-start_name_regexes         .*
-trim_name_regexes          .*BatchNorm.*
-sho

In [0]:
ls -al inference_graph/

total 103424
drwxr-xr-x  3 root root     4096 Jul 15 07:59 ./
drwxr-xr-x 35 root root     4096 Jul 15 08:02 ../
-rw-r--r--  1 root root       77 Jul 15 07:59 checkpoint
-rw-r--r--  1 root root 52383867 Jul 15 07:59 frozen_inference_graph.pb
-rw-r--r--  1 root root 51626500 Jul 15 07:59 model.ckpt.data-00000-of-00001
-rw-r--r--  1 root root    15923 Jul 15 07:59 model.ckpt.index
-rw-r--r--  1 root root  1844932 Jul 15 07:59 model.ckpt.meta
-rw-r--r--  1 root root     3292 Jul 15 07:59 pipeline.config
-rw-r--r--  1 root root      163 Jul 15 06:08 placeholder.txt
drwxr-xr-x  3 root root     4096 Jul 15 07:59 saved_model/


## pb 파일을 로컬로 다운로드하세요(마우스로~)
끝~!